In [1]:
import pandas as pd
import os, json
from transformers import pipeline
from tqdm import tqdm

## Load the dataset

In [ ]:
from datasets import load_dataset

dataset = load_dataset("generative-newsai/news-unmasked")

# Train and test split
test_dataset = dataset["test"]


## Check first 5 rows of the Test dataset

In [3]:
# Check first 5 rows of the test dataset
sample_data = test_dataset[:5]
print(sample_data)

{'image': [<PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=1050x550 at 0x13796D490>, <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=1050x550 at 0x137977700>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=789x412 at 0x137977910>, <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=1050x549 at 0x1379771C0>, <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=1050x550 at 0x137977640>], 'section': ['Television', 'Sports', 'Television', 'Technology', 'Fashion & Style'], 'headline': ["What 's on TV Monday : ' The Voice ' and ' Gentefied '", 'Phillies - Blue Jays Games Postponed After 2 Staff Members Test [MASK]', "Joe Biden 's Run Has [MASK] Night Looking for a Fight", 'Pinterest Posts [MASK] Loss , but Falls Short of Wall St. Estimates', 'Yolanda Foster : Watching Her Daughter Gigi Hadid From the Front Row'], 'image_id': ['00008455-a932-5f2c-b5ce-86584d8345b0', '00040f12-c19e-54db-9513-d4a3d9ce30f1', '0006d6e6-a16f-5d69-a307-0e7e1b659075', '000755c6-df96-502a-a3e

## Load the model

In [5]:
model_name = "mlcorelib/deberta-base-uncased"
unmasker = pipeline('fill-mask', model=model_name)

Some weights of the model checkpoint at mlcorelib/deberta-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


## Unmask the sentences

In [6]:
all_masked_words = []
for each_dict in tqdm(test_dataset):
    sentence = each_dict['headline']  # Get the sentence from the dictionary
    image_id = each_dict['image_id']  # Get the image_id from the dictionary
    if "[MASK]" in sentence: # See if it has a [MASK] in headline
        result = unmasker(sentence)  # Unmask the sentence

        # Make a list of indices where [MASK] is present in the sentence
        # If there are more than one [MASK] in the sentence, then add them as separate entries in the result list
        indices = [i for i, x in enumerate(sentence.split()) if x == "[MASK]"]
        if len(indices) > 1:
            masked_word_idx_list = []
            for i, each_result in enumerate(result):
                # Get the top scoring word
                top_word = each_result[0]['token_str']
                all_masked_words.append([image_id, indices[i], top_word])
        else:
            all_masked_words.append([image_id, indices[0], result[0]['token_str']])

final_masked_words = [l[0] for l in all_masked_words]

100%|██████████| 12247/12247 [05:47<00:00, 35.20it/s]


## Print first 5 rows of the masked words list

In [13]:
print(final_masked_words[:5])

['00040f12-c19e-54db-9513-d4a3d9ce30f1', '0006d6e6-a16f-5d69-a307-0e7e1b659075', '000755c6-df96-502a-a3e4-8f78f0919a8c', '0038ee8b-3f57-5838-a201-509d4bcd1c06', '0048f974-e081-54ee-b0c4-e30b5f66c763']


## Save the results as a dataframe and print first 5 rows of the dataframe

In [15]:
# Save the results in a dataframe with column name id,token_index,token
df = pd.DataFrame(all_masked_words, columns=['id', 'token_index', 'token'])
df.head()

id  token_index    token
0  00040f12-c19e-54db-9513-d4a3d9ce30f1           11        .
1  0006d6e6-a16f-5d69-a307-0e7e1b659075            5      the
2  000755c6-df96-502a-a3e4-8f78f0919a8c            2        a
3  0038ee8b-3f57-5838-a201-509d4bcd1c06            0  regular
4  0048f974-e081-54ee-b0c4-e30b5f66c763            6        a

## Save the dataframe as a csv file

In [16]:
df.to_csv('sample_result.csv', index=False)